In [1]:
import pandas as pd
import joblib
from tools.transformer import TabularTransformer

In [2]:
import plotly.express as px
# import plotly.graph_objs as go
# from plotly.offline import init_notebook_mode

In [3]:
%load_ext autoreload
%autoreload 2

In [3]:
df = pd.read_csv("data/data.csv")

In [4]:
# filtering prices
df = df.loc[(df["PRICE"] > 15) & (df["PRICE"] < 1500), :]

In [5]:
df

ID_PRODUCT  ID_UNIVERSE  ID_CATEGORY  ID_SUBCAT  ID_SUB_SUBCAT  \
1          3247136            1           13        510              0   
2         11459455            1          141        527            216   
3         11117985            2           12         37            139   
4          9775312            2           13        605              0   
5         11285191            1          141         57              0   
...            ...          ...          ...        ...            ...   
175110    14904470            1           12         80             10   
175111    13969831            1           13        510              0   
175112    10478404            2           14         54              0   
175113    13136038            1          141         59            197   
175114    11204374            1           13        506              0   

        ID_BRAND  ID_MODEL  ID_COLOR  ID_MATERIAL  ID_MATERIAL_TYPE  ...  \
1             57         0         3            3                 0  ...   
2              2         0         9            4                 0  ...   
3             47         0       223            1                 0  ...   
4            102         0        14            3                 0  ...   
5             50         0        14           46                 0  ...   
...          ...       ...       ...          ...               ...  ...   
175110      2731         0         9            2                 0  ...   
175111         6      4114       225            4                 0  ...   
175112      6444         0         3           46                 0  ...   
175113        57         0         2           16                 0  ...   
175114        60         0         9           19                 0  ...   

        ID_SIZE_TYPE  GEO2_SELLER  HOURS_ONLINE  ORDER_CURRENCY   DATE_SOLD  \
1                 38          soe         32942             gbp  2020-08-21   
2                  0          soe           133             usd  2020-08-26   
3                147          roe           775             usd  2020-08-18   
4                 56          soe          3206             eur  2020-08-03   
5                  0       france             4             usd  2020-08-03   
...              ...          ...           ...             ...         ...   
175110             7           us           194             usd  2021-03-19   
175111            34       france          1939             usd  2021-04-12   
175112           106          soe           172             eur  2020-06-01   
175113             0          roe           104             eur  2020-12-06   
175114            39          soe          1144             eur  2020-09-11   

        YEAR  MONTH  DAY_OF_MONTH DAY_OF_WEEK  PRICE  
1       2020      8            21           5    113  
2       2020      8            26           3    298  
3       2020      8            18           2    133  
4       2020      8             3           1     75  
5       2020      8             3           1     91  
...      ...    ...           ...         ...    ...  
175110  2021      3            19           5     21  
175111  2021      4            12           1    147  
175112  2020      6             1           1     95  
175113  2020     12             6           0    241  
175114  2020      9            11           5    125  

[171980 rows x 27 columns]

In [6]:
px.histogram(df, x="PRICE", title="Histogram")

In [11]:
from sklearn.preprocessing import PowerTransformer
import numpy as np

pow_trans = PowerTransformer(method="box-cox")

In [14]:
df["PRICE_NORM"] = pow_trans.fit_transform(df["PRICE"].values.reshape(len(df), 1)).flatten()
df["PRICE_LOG"] = df["PRICE"].apply(lambda x: np.log(x))
df["PRICE_2LOG"] = df["PRICE_LOG"].apply(lambda x: np.log(x))

In [15]:
px.histogram(df, x="PRICE_2LOG", title="Histogram")

In [ ]:
df.columns

In [6]:
tt = TabularTransformer(
    numeric=["HOURS_ONLINE"],
    dates=["DATE_SOLD"],
    ordinal=["ID_UNIVERSE", "ID_CATEGORY", "ID_SUBCAT", "ID_SUB_SUBCAT", "ID_BRAND", "ID_MODEL", "ID_COLOR", "ID_MATERIAL", "ID_MATERIAL_TYPE", "ID_CONDITION", "VINTAGE", "ID_BRACELET", "ID_BOX", "ID_MECHANISM", "ID_SIZE_TYPE", "GEO2_SELLER", "ORDER_CURRENCY"], # ordinal
    cat=[], # one-hot
    highcat=[]
)

In [7]:
input_list = tt.fit_transform(df)

In [10]:
# saving preprocessor
joblib.dump(tt, 'models/preprocess.pkl', compress=1)

['models/preprocess.pkl']

In [ ]:
len(input_list)

In [ ]:
# print([(item.shape, item.dtype) for item in input_list])

In [8]:
df_transformed = pd.DataFrame(input_list, columns=tt.columns)
# df_transformed[tt.columns[1][0]] = input_list[1]
# df_transformed[tt.columns[1][1]] = input_list[2]

In [9]:
df_transformed

HOURS_ONLINE  DATE_SOLD_day_sin  DATE_SOLD_day_cos  \
0           1.374887          -0.485302          -0.874347   
1           2.153557          -0.897805          -0.440394   
2          -0.581196          -0.848644           0.528964   
3           0.070862          -0.485302          -0.874347   
4           0.700494           0.571268           0.820763   
...              ...                ...                ...   
173735     -0.448972          -0.651372          -0.758758   
173736      0.463826           0.651372          -0.758758   
173737     -0.488263           0.201299           0.979530   
173738     -0.658630           0.937752           0.347305   
173739      0.232866           0.790776          -0.612106   

        DATE_SOLD_dayofweek_sin  DATE_SOLD_dayofweek_cos  DATE_SOLD_month_sin  \
0                  8.660254e-01                      0.5        -8.660254e-01   
1                 -8.660254e-01                     -0.5        -8.660254e-01   
2                  8.660254e-01                     -0.5        -8.660254e-01   
3                  8.660254e-01                      0.5        -8.660254e-01   
4                  0.000000e+00                      1.0        -8.660254e-01   
...                         ...                      ...                  ...   
173735            -8.660254e-01                     -0.5         1.000000e+00   
173736             0.000000e+00                      1.0         8.660254e-01   
173737             0.000000e+00                      1.0         1.224647e-16   
173738            -2.449294e-16                      1.0        -2.449294e-16   
173739            -8.660254e-01                     -0.5        -1.000000e+00   

        DATE_SOLD_month_cos  DATE_SOLD_year  ID_UNIVERSE  ID_CATEGORY  ...  \
0             -5.000000e-01             0.5          1.0          1.0  ...   
1             -5.000000e-01             0.5          1.0          2.0  ...   
2             -5.000000e-01             0.5          1.0          4.0  ...   
3             -5.000000e-01             0.5          2.0          1.0  ...   
4             -5.000000e-01             0.5          2.0          2.0  ...   
...                     ...             ...          ...          ...  ...   
173735         6.123234e-17             1.0          1.0          1.0  ...   
173736        -5.000000e-01             1.0          1.0          2.0  ...   
173737        -1.000000e+00             0.5          2.0          3.0  ...   
173738         1.000000e+00             0.5          1.0          4.0  ...   
173739        -1.836970e-16             0.5          1.0          2.0  ...   

        ID_MATERIAL  ID_MATERIAL_TYPE  ID_CONDITION  VINTAGE  ID_BRACELET  \
0              10.0               0.0           2.0      0.0          0.0   
1              23.0               0.0           2.0      0.0          0.0   
2              32.0               0.0           4.0      1.0          0.0   
3               1.0               0.0           1.0      0.0          0.0   
4              23.0               0.0           2.0      0.0          0.0   
...             ...               ...           ...      ...          ...   
173735         12.0               0.0           2.0      0.0          0.0   
173736         32.0               0.0           6.0      0.0          0.0   
173737         39.0               0.0           1.0      0.0          0.0   
173738          8.0               0.0           2.0      0.0          0.0   
173739         11.0               0.0           6.0      0.0          0.0   

        ID_BOX  ID_MECHANISM  ID_SIZE_TYPE  GEO2_SELLER  ORDER_CURRENCY  
0          0.0           0.0         201.0         11.0            10.0  
1          0.0           0.0         164.0          9.0             5.0  
2          0.0           0.0           0.0          9.0            11.0  
3          0.0           0.0          34.0          7.0            11.0  
4          0.0           0.0         185.0          9.0   

In [ ]:
# adding PRICE data
df_transformed["PRICE"] = df["PRICE"]
df_transformed["ID_PRODUCT"] = df["ID_PRODUCT"]

df_transformed

In [ ]:
df_transformed.to_csv("data/data_encoded.csv", index=False)